In [1]:
import plotly.graph_objects as go
import numpy as np
import matplotlib.pyplot as plt
import pandas as pd

<h2> Base imports

In [11]:

data_df = pd.read_pickle("Kris_merged_yolov8.pkl")
data_df

image name  car_count      timestamp_true
0     Kris_1206-1423.png         14 2023-06-12 14:23:00
1     Kris_1008-0950.png         32 2023-08-10 09:50:00
2     Kris-2410-0502.png         14 2023-10-24 05:02:00
3     Kris_1108-0124.png          8 2023-08-11 01:24:00
4     Kris_2406-2128.png          1 2023-06-24 21:28:00
...                  ...        ...                 ...
1826  Kris-2510-1437.png         47 2023-10-25 14:37:00
1827  Kris-1610-0035.png          8 2023-10-16 00:35:00
1828  Kris_0806-2233.png          0 2023-06-08 22:33:00
1829  Kris_0706-0712.png          0 2023-06-07 07:12:00
1830  Kris-1610-2126.png         10 2023-10-16 21:26:00

[1831 rows x 3 columns]

In [12]:
data_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1831 entries, 0 to 1830
Data columns (total 3 columns):
 #   Column          Non-Null Count  Dtype         
---  ------          --------------  -----         
 0   image name      1831 non-null   object        
 1   car_count       1831 non-null   int64         
 2   timestamp_true  1831 non-null   datetime64[ns]
dtypes: datetime64[ns](1), int64(1), object(1)
memory usage: 43.0+ KB


In [13]:
data_df

image name  car_count      timestamp_true
0     Kris_1206-1423.png         14 2023-06-12 14:23:00
1     Kris_1008-0950.png         32 2023-08-10 09:50:00
2     Kris-2410-0502.png         14 2023-10-24 05:02:00
3     Kris_1108-0124.png          8 2023-08-11 01:24:00
4     Kris_2406-2128.png          1 2023-06-24 21:28:00
...                  ...        ...                 ...
1826  Kris-2510-1437.png         47 2023-10-25 14:37:00
1827  Kris-1610-0035.png          8 2023-10-16 00:35:00
1828  Kris_0806-2233.png          0 2023-06-08 22:33:00
1829  Kris_0706-0712.png          0 2023-06-07 07:12:00
1830  Kris-1610-2126.png         10 2023-10-16 21:26:00

[1831 rows x 3 columns]

<h2> Feature Engineering

In [14]:
# --> handling index and timestamps first

data_df.reset_index(inplace=True)

data_df.drop(columns=["index","image name"], inplace=True)


data_df.set_index("timestamp_true", inplace=True)


data_df.sort_index(ascending=True, inplace= True)

# convert the timestamp into unix epoch, to minute level precision
data_df['num_timestamp'] =  (pd.to_datetime(data_df.index) - pd.Timestamp("1970-01-01")) // pd.Timedelta('1min')

# # --> type setting for vars
data_df["car_count"] = data_df["car_count"]

# # --> deriving features

data_df["month_no"] = data_df.index.month

data_df["month_name"] = data_df.index.month_name()

data_df["day"] = data_df.index.day

data_df["day_of_week"] = data_df.index.dayofweek

data_df["day_of_week_name"] = data_df.index.day_name()

data_df["is_weekend"] = np.where(
    data_df.index.isin(["Sunday", "Saturday"]), 1, 0
)
data_df["hour_of_day"] = data_df.index.hour

data_df['minutes'] = data_df.index.minute


data_df["min_of_day"] = data_df['hour_of_day'] * 60 + data_df['minutes']

data_df['week_no']=  data_df.index.weekday

In [15]:
# Combine the columns in the desired format
data_df['combined'] = data_df.apply(lambda row: f"{str(row['month_no']).zfill(2)}{str(row['day']).zfill(2)}{str(row['hour_of_day']).zfill(2)}{str(row['minutes']).zfill(2)}", axis=1)



In [16]:
data_df.head()

car_count  num_timestamp  month_no month_name  day  \
timestamp_true                                                            
2023-06-06 20:36:00          0       28101396         6       June    6   
2023-06-06 21:06:00          9       28101426         6       June    6   
2023-06-06 21:37:00          0       28101457         6       June    6   
2023-06-06 22:07:00          7       28101487         6       June    6   
2023-06-06 22:37:00          2       28101517         6       June    6   

                     day_of_week day_of_week_name  is_weekend  hour_of_day  \
timestamp_true                                                               
2023-06-06 20:36:00            1          Tuesday           0           20   
2023-06-06 21:06:00            1          Tuesday           0           21   
2023-06-06 21:37:00            1          Tuesday           0           21   
2023-06-06 22:07:00            1          Tuesday           0           22   
2023-06-06 22:37:00            1          Tuesday           0           22   

                     minutes  min_of_day  week_no  combined  
timestamp_true                                               
2023-06-06 20:36:00       36        1236        1  06062036  
2023-06-06 21:06:00        6        1266        1  06062106  
2023-06-06 21:37:00       37        1297        1  06062137  
2023-06-06 22:07:00        7        1327        1  06062207  
2023-06-06 22:37:00       37        1357        1  06062237

In [17]:
lengths = data_df['combined'].str.len()
unique_lengths = lengths.value_counts()
unique_lengths

combined
8    1831
Name: count, dtype: int64

In [18]:
# --> convert unix epoch time back to our timestamp format
# 
# pd.Timestamp("1970-01-01") + pd.to_timedelta(data_df['num_timestamp'][1], unit='min')

In [21]:

# Create the plot
fig = go.Figure()

# Create the line chart using Plotly Express
fig.add_trace(go.Scatter( x=data_df.index, y=data_df['car_count'], mode='lines+markers' ,marker=dict(symbol='cross', size=5),name = "Count over time"))
# Layout and titles
fig.update_layout(title='Car count distribution',
                  xaxis_title='timestamp',
                  yaxis_title='car_count',
                  showlegend=True,
                  height = 600
                  )
# Show the plot
fig.show()

In [20]:
# Create the plot
fig = go.Figure()

# Create the line chart using Plotly Express
fig.add_trace(go.Scatter( x=data_df['num_timestamp'], y=data_df['car_count'], mode='lines+markers' ,marker=dict(symbol='cross', size=3)))

# Show the plot
fig.show()

In [22]:
 #Create the plot
fig = go.Figure()

# Create the line chart using Plotly Express
fig.add_trace(go.Histogram(x=data_df['car_count'], name='car count dist'))

# Layout and titles
fig.update_layout(title='Car count distribution',
                  xaxis_title='num_timestamp',
                  yaxis_title='car_count',
                  showlegend=True)


# Show the plot
fig.show()

In [23]:
def plot_rolling_statistics(df, hours_list):
    fig = go.Figure()
    
    # Original data
    fig.add_trace(go.Scatter(x=df.index, y=df['car_count'], mode='lines', name='Original Data'))
    
    # RGB values for the colors
    color_dict = {
        hours_list[0]: '39, 176, 245',  # blue
        hours_list[1]: '245, 40, 145', # red
        hours_list[2]: '39, 245, 99'  # green
    }
    
    for hours in hours_list:
        window_str = f"{hours}H"
        
        # Calculate rolling statistics
        rolling_mean = df['car_count'].rolling(window=window_str).mean()
        rolling_std = df['car_count'].rolling(window=window_str).std()
        
        # Get the RGB value for the current window size
        color_rgb = color_dict.get(hours, '0,0,0')  # default to black if not found
        
        # Visualization
        legend_group = f"group_{hours}"
        
        fig.add_trace(go.Scatter(x=df.index,
                                 y=rolling_mean,
                                 mode='lines',
                                 line=dict(color=f'rgb({color_rgb})',
                                           width= 3),
                                 name=f'{window_str} Rolling Mean',
                                 legendgroup=legend_group
                                 ))
        
        fig.add_trace(go.Scatter(x=df.index,
                                 y=rolling_mean + rolling_std,
                                 mode='lines',
                                 fill= 'tonexty',
                                 fillcolor= f'rgba({color_rgb}, 0.2)',
                                 line=dict(color=f'rgba({color_rgb}, 0.8)',
                                           dash= 'dash',
                                           width= 2,),
                                 name=f'+1 std ({window_str})',
                                 legendgroup=legend_group
                                 ))
        
        fig.add_trace(go.Scatter(x=df.index,
                                 y=rolling_mean - rolling_std,
                                 mode='lines',
                                 fill= 'tonexty',
                                 fillcolor= f'rgba({color_rgb}, 0.2)',
                                 line=dict(color=f'rgba({color_rgb}, 0.8)',
                                           dash= 'dash',
                                           width= 2),
                                 name=f'-1 std ({window_str})',
                                 legendgroup=legend_group
                                 ))
        
        
        
    fig.update_layout(title='Rolling Statistics Plot', xaxis_title='Timestamp', yaxis_title='Car Count', height=800)
    fig.show()

# Usage:
plot_rolling_statistics(data_df, [3, 6, 24])


<h2>Experiment --> 2


<p>data split


In [16]:
from plotly.subplots import make_subplots
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler


# Assuming data_df is your DataFrame
data_df = data_df.sort_index()  # Ensure the data is sorted by timestamp

# feature to shift the mean on y axis to 0, normalization 
data_df['centered_car_count'] = data_df['car_count'] - data_df['car_count'].mean() 
data_length = len(data_df)

# Splitting the data into training (70%), validation (15%), and test (15%) sets
train = data_df.iloc[:int(0.7 * data_length)]
valid = data_df.iloc[int(0.7 * data_length):int(0.8 * data_length)]
test = data_df.iloc[int(0.8 * data_length):]

# Extracting the features and target variable for each split
X_train = train['num_timestamp'].values.reshape(-1,1)
y_train = train['car_count']
X_valid = valid['num_timestamp'].values.reshape(-1,1)
y_valid = valid['car_count']
X_test  = test['num_timestamp']
y_test = test['car_count']



In [17]:
# Create a line chart to visualize the train-validation-test split using Plotly graph objects
fig = go.Figure()

# Plotting the training data
fig.add_trace(go.Scatter(x=train['num_timestamp'], y=y_train, mode='lines', name='Train Data', line=dict(color='blue')))

# Plotting the validation data
fig.add_trace(go.Scatter(x=valid['num_timestamp'], y=y_valid, mode='lines', name='Validation Data', line=dict(color='green')))

# Plotting the test data
fig.add_trace(go.Scatter(x=test['num_timestamp'], y=y_test, mode='lines', name='Test Data', line=dict(color='red')))

# Setting the layout for the plot
fig.update_layout(title='Train-Validation-Test Split Visualization', xaxis_title='Timestamp', yaxis_title='Count')

# Display the plot
fig.show()

In [18]:
type(data_df['num_timestamp'][1])

numpy.longlong

<h2>Exp 2:  Training

In [19]:
# helper functions
from sklearn.gaussian_process import GaussianProcessRegressor
from sklearn.gaussian_process.kernels import RBF
from sklearn.metrics import mean_absolute_error, mean_squared_error, r2_score

import plotly.subplots as sp
from sklearn.metrics import mean_absolute_error, mean_squared_error, r2_score

def plot_evaluation_metrics(gpr_model, y_true, y_pred):
    ''' 
        This function will take the gpr model and true values and predicted values to create 
    '''
    # Calculate residuals
    residuals = y_true - y_pred

    # Calculate metrics
    r2 = r2_score(y_true, y_pred)
    log_marginal_likelihood = gpr_model.log_marginal_likelihood(gpr_model.kernel_.theta)
    mae = mean_absolute_error(y_true, y_pred)
    mse = mean_squared_error(y_true, y_pred)
    rmse = np.sqrt(mse)
    kernel = gpr_model.kernel_

    # Create subplots with an additional column for metrics
    fig = sp.make_subplots(rows=1, cols=2, column_widths=[0.5, 0.5], subplot_titles=("Residuals", "Predicted vs Actual"))

    # Plot residuals
    fig.add_trace(
        go.Scatter(
            x=y_pred,
            y=residuals,
            mode='markers',
            name='Residuals ',
            marker=dict(color='blue')
        ),
        row=1, col=1
    )
    # Add mean line to residuals plot
    fig.add_trace(
        go.Scatter(
            x=y_pred,
            y=[residuals.mean()]*len(y_pred),
            mode='lines',
            name='Mean Residual',
            line=dict(color='green', dash='dash')
        ),
        row=1, col=1
    )

    # Plot predicted vs actual values
    fig.add_trace(
        go.Scatter(
            x=y_true,
            y=y_pred,
            mode='markers',
            name='Predicted vs Actual ',
            marker=dict(color='red')
        ),
        row=1, col=2
    )
    # Add line y=x to predicted vs actual plot
    fig.add_trace(
        go.Scatter(
            x=y_true,
            y=y_true,
            mode='lines',
            name='y=x line',
            line=dict(color='green', dash='dash')
        ),
        row=1, col=2
    )

    # Add metrics as text in the third column
    metrics_text = f"R-squared: {r2:.2f} | "\
                f"LML: {log_marginal_likelihood:.2f} | "\
                f"MAE: {mae:.2f} | "\
                f"MSE: {mse:.2f} | "\
                f"RMSE: {rmse:.2f} | "\
                #f"Learned kernel: {kernel} |"
    
    fig.add_annotation(dict(font=dict(size=15),
                                        x=0,
                                        y=-0.14,
                                        showarrow=False,
                                        text= metrics_text,
                                        textangle=0,
                                        xanchor='left',
                                        xref="paper",
                                        yref="paper"))
    
    fig.add_annotation(dict(font=dict(size=15),
                                        x=0,
                                        y=1.08,
                                        showarrow=False,
                                        text= f"Learned kernel: {kernel}" ,
                                        textangle=0,
                                        xanchor='left',
                                        xref="paper",
                                        yref="paper"))
        
    
    

    # Update layout
    fig.update_layout(title="Model Evaluation Metrics", height=700)
    fig.update_xaxes(title_text="Predicted Values ", row=1, col=1)
    fig.update_yaxes(title_text="Residuals", row=1, col=1)
    fig.update_xaxes(title_text="Actual Values", row=1, col=2)
    fig.update_yaxes(title_text="Predicted Values", row=1, col=2)
    fig.show()

def plot_gpr_samples_plotly( gpr_model, n_samples, X_train, y_train):
    '''
        Plots samples from a Gaussian Process Regression model using Plotly. By default plots from a distribution if gpr is not trained.
    '''
    
    x = x = np.linspace(X_train.min(), X_train.max(), len(X_train)) # field to draw out prior and posteriors 
    X = x.reshape(-1,1)

    y_mean, y_std = gpr_model.predict( X, return_std=True)
    y_samples = gpr_model.sample_y( X, n_samples)

    fig = go.Figure()
   
    for idx, single_prior in enumerate(y_samples.T):
        fig.add_trace(
            go.Scatter(
                x=x, y=single_prior, mode="lines", name=f"Sampled function #{idx + 1}"
            )
        )

    fig.add_trace(
        go.Scatter(
            x=x,
            y=y_mean,
            mode="lines",
            line_color="red",
            name="Mean",
            line=dict(dash="dash"),
        )
    )

    fig.add_trace(
        go.Scatter(
            x=x,
            y=y_mean - y_std,
            fill=None,
            mode="lines",
            line_color="rgba(255,0,0,0.1)",
            showlegend=False,
        )
    )

    fig.add_trace(
        go.Scatter(
            x=x,
            y=y_mean + y_std,
            fill="tonexty",
            mode="lines",
            line_color="rgba(173, 216, 230, 0.5)",
            name=r"uncertainty",
        )
    )

    fig.add_trace(
        go.Scatter(
            x=X_train.ravel(),
            y=y_train.ravel(),
            mode='markers',
            name="Training Data",
            marker=dict(symbol='cross', size=4, color= 'royalblue')
        )
    )
    
    fig.add_trace(
        go.Scatter(
            x=X_train.ravel(),
            y=y_train.ravel(),
            mode='lines',
            name="Training Data Signal",
            marker=dict(symbol='cross', size=4, color= 'royalblue')
        )
    )
    
    # fig.add_trace(
    #     go.Scatter(
    #         x=X_test.ravel(),
    #         y=y_test.ravel(),
    #         mode='lines+markers',
    #         name="Test Data",
    #         marker=dict(symbol='cross', size=4, color= 'green')
    #     )
    # )

    fig.update_layout(
        xaxis_title="Unix Epoch time",
        yaxis_title="Count",
        height= 800,
    )

    fig.show()

def gpr_train(gpr, x_train, y_train, x_test, y_test):
    '''
        Trains a Gaussian Process Regressor on the given training data and makes predictions on test data. 
    '''
    # Create the GPR model outside this func to have more control over kernels

    # Fit the GPR model to the training data
    gpr.fit(x_train, y_train)
    
    plot_gpr_samples_plotly(gpr, 5,x_train,y_train)
    # Perform predictions using the trained GPR model
    y_pred, y_std = gpr.predict(x_test, return_std=True)
    # y_pred: Predicted target values
    # y_std: Standard deviation of predictions

    # Access learned model properties
    kernel_params = gpr.kernel_  # Learned kernel parameters
    # noise_level = gpr.kernel_.get_params()['k2_noise_level']  # Estimated noise level (if available)
    noise_level = gpr.alpha_  # Estimated noise level (if available)

    mae = mean_absolute_error(y_test, y_pred)
    mse = mean_squared_error(y_test, y_pred)
    rmse = np.sqrt(mse)
    r2 = r2_score(y_test, y_pred)
    mape = np.mean(np.abs((y_test - y_pred) / y_test)) * 100
    lml = gpr.log_marginal_likelihood(gpr.kernel_.theta)

    # evaluation metrics
    print(f"MAE: {mae}") # 
    print(f"MSE: {mse}")
    print(f"RMSE: {rmse}")
    print(f"R-squared: {r2}")
    print(f"MAPE: {mape}%")
    print(f"Kernel parameters after fit: \n{gpr.kernel_} \n")
    print(f"noise level: {noise_level}")
    print(f'LML: {lml}')

    # Print or analyze the results as needed
    print("Predicted values:", y_pred)
    # print("Prediction uncertainty (std):", y_std)
    print("Learned kernel parameters:", kernel_params)
    # print("Estimated noise level:", noise_level)

    return y_pred, y_std, gpr

In [20]:
# scales are off, y is up too high 
# scaling time baby!!!

In [21]:
# # Subtracting the mean from the 'car_count' column
# data_df['centered_car_count'] = data_df['car_count'] - data_df['car_count'].mean()

# Now, you can use 'centered_car_count' as your target variable for modeling.
# Extracting the features and target variable for each split
X_train_norm  = train['num_timestamp'].values.reshape(-1,1)
y_train_norm  = train['centered_car_count']
X_valid_norm  = valid['num_timestamp'].values.reshape(-1,1)
y_valid_norm  = valid['centered_car_count']
X_test_norm  = test['num_timestamp'].values.reshape(-1,1)
y_test_norm  = test['centered_car_count']


In [22]:

rbf_kernel = 10.0**2 * RBF(length_scale=1, length_scale_bounds= (1e-1, 50))

gpr = GaussianProcessRegressor(kernel=rbf_kernel, n_restarts_optimizer= 10)

# fig = go.Figure(data=go.Scatter(x=x, y=x, mode="markers"))
# fig.show()
plot_gpr_samples_plotly(gpr, 5, X_train_norm, y_train_norm)


y_pred, y_std, gpr_model = gpr_train( gpr, X_train_norm ,y_train_norm, X_test_norm, y_test_norm)


MAE: 10.81886342336202
MSE: 145.63617106573687
RMSE: 12.067981234064664
R-squared: -0.0004939226921143458
MAPE: 100.0%
Kernel parameters after fit: 
10.5**2 * RBF(length_scale=0.539) 

noise level: [-0.07248851 -0.03645365 -0.08149723 -0.05447108 -0.0634798  -0.07248851
 -0.07248851 -0.09050595 -0.09050595 -0.09050595 -0.09050595 -0.08149723
 -0.09050595 -0.07248851 -0.02744494  0.0536335   0.01759864  0.03561607
 -0.00041879 -0.00041879 -0.05447108 -0.00041879 -0.04546237  0.0536335
  0.09867707  0.0536335   0.10768579  0.07165093  0.08966836  0.12570322
  0.13471193  0.10768579  0.17074679  0.2338078   0.15272936  0.13471193
  0.19777294  0.18876422  0.20678165  0.17975551  0.2338078   0.08065964
  0.10768579  0.03561607  0.04462478  0.02660735 -0.05447108 -0.02744494
 -0.0634798   0.01759864 -0.09050595  0.00858992 -0.02744494 -0.02744494
 -0.03645365 -0.02744494 -0.01843622 -0.02744494 -0.03645365 -0.04546237
 -0.00942751  0.02660735  0.07165093  0.12570322  0.13471193  0.12570322


In [23]:
from sklearn.gaussian_process.kernels import ExpSineSquared
ex_sin_kernel =  ExpSineSquared(length_scale=1.0,length_scale_bounds=(1e-1, 50) , periodicity=0.5, periodicity_bounds= (1e-1, 50))
gpr = GaussianProcessRegressor(kernel=ex_sin_kernel, n_restarts_optimizer= 10)

# fig = go.Figure(data=go.Scatter(x=x, y=x, mode="markers"))
# fig.show()
plot_gpr_samples_plotly(gpr, 5, X_train_norm, y_train_norm)


y_pred, y_std, gpr_model = gpr_train( gpr, X_train_norm ,y_train_norm, X_test_norm, y_test_norm)


MAE: 10.807293608087674
MSE: 147.55757387215095
RMSE: 12.14732784904363
R-squared: -0.013693609396272066
MAPE: 101.93393593215117%
Kernel parameters after fit: 
ExpSineSquared(length_scale=5.72, periodicity=30.2) 

noise level: [-1.04052877e+11 -6.65753617e+10 -1.10594144e+11 -8.02282491e+10
 -9.08185361e+10 -1.01672828e+11 -1.03789264e+11 -1.21972908e+11
 -1.20842803e+11 -1.20230152e+11 -1.30509796e+11 -1.17143018e+11
 -1.24687005e+11 -1.23623355e+11 -6.96062730e+10  2.46880281e+10
 -3.85091652e+10 -1.41076685e+10 -4.97745158e+10 -4.52842937e+10
 -1.26802624e+11 -6.35001924e+10 -1.09613341e+11 -1.40017523e+10
  3.75568929e+10 -1.05257683e+10  4.73658833e+10  5.87590250e+09
  2.53047296e+10  6.56942687e+10  8.34820201e+10  5.01970312e+10
  1.18059911e+11  2.08814715e+11  1.13487513e+11  8.85950078e+10
  1.89825402e+11  1.73018017e+11  1.86846280e+11  1.50622902e+11
  2.44933350e+11  6.84857205e+10  9.19833235e+10  5.61112546e+09
  4.98447551e+10  2.38999490e+10 -7.24748962e+10 -1.31643

In [24]:
from sklearn.gaussian_process.kernels import RBF, WhiteKernel, ExpSineSquared, ConstantKernel as C

# RBF kernel with a length scale of 1.0
k1 = 1.0 * RBF(length_scale=0.5, length_scale_bounds=(1e-3, 1e3))

# White kernel to account for noise
k2 = WhiteKernel(noise_level=1, noise_level_bounds=(1e-10, 1e+1))

# Periodic kernel
k3 = ExpSineSquared(length_scale=1.0,
                    length_scale_bounds=(1e-1, 50) ,
                    periodicity=0.5,
                    periodicity_bounds= (1e-1, 50))

# Combined kernel
kernel = k1 + k2 + k3

gpr = GaussianProcessRegressor(kernel=kernel, n_restarts_optimizer= 10)

# fig = go.Figure(data=go.Scatter(x=x, y=x, mode="markers"))
# fig.show()
# plot_gpr_samples_plotly(gpr, 5, X_train_norm, y_train_norm)


# y_pred, y_std, gpr_model = gpr_train( gpr, X_train_norm ,y_train_norm, X_test_norm, y_test_norm)


<h2> Exp2: Results and plots

In [25]:
plot_gpr_samples_plotly(gpr, 5, X_train_norm, y_train_norm)

In [26]:

y_pred, y_std, gpr_model = gpr_train( gpr, X_train_norm ,y_train_norm, X_test_norm, y_test_norm)

MAE: 10.744819678644715
MSE: 143.88574862060273
RMSE: 11.995238581228918
R-squared: 0.01153116012683808
MAPE: 101.1384961286549%
Kernel parameters after fit: 
10.5**2 * RBF(length_scale=0.006) + WhiteKernel(noise_level=0.00549) + ExpSineSquared(length_scale=0.1, periodicity=0.167) 

noise level: [-7.58276870e-02 -3.98516593e-02 -8.76221057e-02 -6.50208048e-02
 -7.10080824e-02 -8.21034231e-02 -8.09255624e-02 -1.00710637e-01
 -9.64624243e-02 -1.00019249e-01 -9.20810745e-02 -8.38800953e-02
 -9.38528851e-02 -7.65341894e-02 -2.39238431e-02  5.71326177e-02
  1.80363076e-02  3.60096129e-02  2.13420799e-03 -2.04462712e-04
 -5.33716115e-02  5.94105377e-03 -4.23655463e-02  5.88691605e-02
  1.00050278e-01  5.94012687e-02  1.10440817e-01  7.53378871e-02
  9.58377643e-02  1.31129841e-01  1.35469635e-01  1.09308554e-01
  1.74572174e-01  2.31984557e-01  1.49168698e-01  1.32671234e-01
  1.90189420e-01  1.86535213e-01  2.01424022e-01  1.75753702e-01
  2.32085611e-01  7.78663661e-02  1.02296060e-01  3.1

In [27]:
# Calculate residuals
residuals = y_test - y_pred
 
# Create a plotly figure
fig = go.Figure()

# Actual vs Predicted values
fig.add_trace(go.Scatter(y=y_test_norm, x=y_pred, mode='markers', name='Actual(test) vs Predicted'))


# Residuals

fig.add_trace(go.Scatter(y=residuals, x=y_test_norm, mode='markers',name='Residuals', marker=dict(symbol='cross', size=4)))

# Horizontal line at y=0 for Residual plot
fig.add_trace(
    go.Scatter(x=y_test_norm, y=[0]*50, mode='lines', name='Zero Line', line=dict(color='orange',dash='dash')))

# Layout and titles
fig.update_layout(title='Actual vs Predicted & Residuals',
                  xaxis_title= 'Actual Values',
                  yaxis_title='Predicted Values',
                  showlegend=True)


fig.show()

# Print out the RMSE for evaluation
rmse = mean_squared_error(y_test, y_pred, squared=False)
print(f"Root Mean Squared Error (RMSE): {rmse}")

Root Mean Squared Error (RMSE): 17.492706873707647


In [28]:
# Plotting histogram of residuals
fig = go.Figure(data=[go.Histogram(x=residuals)])
fig.update_layout(title='Histogram of Residuals',
                  xaxis_title='Residual',
                  yaxis_title='Frequency')
fig.show()

In [29]:
# Create a plotly graph
fig = go.Figure()

# Actual test values
fig.add_trace(go.Scatter(x=X_test_norm[:, 0], y=y_test_norm, mode='markers', name='Actual Values', marker=dict(symbol='cross', size=4, color= 'royalblue')))

# Predicted values
fig.add_trace(go.Scatter(x=X_test_norm[:, 0], y=y_pred, mode='markers', name='Predicted Values',marker=dict(symbol='cross', size=4, color= 'red')))

# Confidence intervals
fig.add_trace(go.Scatter(x=X_test_norm[:, 0], y=y_pred + 1.96*y_std, mode='lines', line=dict(dash='dash'), name='Upper Confidence Interval'))
fig.add_trace(go.Scatter(x=X_test_norm[:, 0], y=y_pred - 1.96*y_std, mode='lines', line=dict(dash='dash'), name='Lower Confidence Interval'))

# Update layout
fig.update_layout(title='GPR Fit on Test Data', xaxis_title='X', yaxis_title='Y')
fig.show()

In [30]:
# import numpy as np
# import plotly.graph_objects as go
# from sklearn.gaussian_process import GaussianProcessRegressor
# from sklearn.gaussian_process.kernels import RBF, WhiteKernel, ExpSineSquared

# # Generate LML matrices for each kernel component
# n0 = 60
# theta0 = np.logspace(-3, 9, n0)  # Length scale for RBF
# theta1 = np.logspace(-3, 9, n0)  # Noise level for WhiteKernel
# theta2 = np.logspace(-3, 9, n0)  # Length scale for ExpSineSquared
# theta3 = np.logspace(-3, 9, n0)  # Periodicity for ExpSineSquared

# Theta0, Theta1 = np.meshgrid(theta0, theta1)
# Theta2, Theta3 = np.meshgrid(theta2, theta3)

# LML_rbf = np.zeros((n0, n0))
# LML_white = np.zeros((n0, n0))
# LML_exp_sine = np.zeros((n0, n0))

# for i in range(n0):
#     for j in range(n0):
#         # Current hyperparameters of the model
#         current_theta = gpr_model.kernel_.theta
        
#         # For RBF kernel
#         theta_rbf = np.log([Theta0[i, j]])
#         complete_theta_rbf = np.concatenate([current_theta[1:], theta_rbf ])
#         LML_rbf[i, j] = gpr_model.log_marginal_likelihood(complete_theta_rbf)
        
#         # For WhiteKernel
#         theta_white = np.log([Theta1[i, j]])
#         complete_theta_white = np.concatenate([np.array([current_theta[0]]), theta_white, current_theta[2:3]])
#         LML_white[i, j] = gpr_model.log_marginal_likelihood(complete_theta_white)
        
        
#         # For ExpSineSquared kernel
#         theta_exp_sine = np.log([Theta2[i, j], Theta3[i, j]])
#         complete_theta_exp_sine = np.concatenate([current_theta[:2], theta_exp_sine])
#         LML_exp_sine[i, j] = gpr_model.log_marginal_likelihood(complete_theta_exp_sine)

# # Visualization using Plotly
# fig = go.Figure()

# # LML heatmap for RBF kernel
# fig.add_trace(go.Contour(z=LML_rbf, x=theta0, y=theta1, colorscale='Viridis', name='RBF'))

# # LML heatmap for WhiteKernel
# fig.add_trace(go.Contour(z=LML_white, x=theta0, y=theta1, colorscale='Viridis', name='WhiteKernel'))

# # LML heatmap for ExpSineSquared kernel
# fig.add_trace(go.Contour(z=LML_exp_sine, x=theta2, y=theta3, colorscale='Viridis', name='ExpSineSquared'))

# fig.update_layout(title='Log Marginal Likelihood Heatmaps', xaxis_title='Length Scale / Noise Level', yaxis_title='Length Scale / Periodicity')
# fig.show()



In [31]:
# # type(gpr_model.kernel_)
# gpr_model.kernel_

In [32]:
# gpr_model.kernel_.theta
# gpr_model.log_marginal_likelihood(theta=gpr_model.kernel_.theta , eval_gradient=True)

In [33]:
# import numpy as np
# import plotly.graph_objects as go
# from sklearn.gaussian_process import GaussianProcessRegressor
# from sklearn.gaussian_process.kernels import RBF, WhiteKernel, ExpSineSquared

# # Generate LML matrices for each kernel component
# n0 = 60
# theta0 = np.logspace(-3, 9, n0)  # Length scale for RBF
# theta1 = np.logspace(-3, 9, n0)  # Noise level for WhiteKernel
# theta2 = np.logspace(-3, 9, n0)  # Length scale for ExpSineSquared
# theta3 = np.logspace(-3, 9, n0)  # Periodicity for ExpSineSquared

# Theta0, Theta1 = np.meshgrid(theta0, theta1)
# Theta2, Theta3 = np.meshgrid(theta2, theta3)

# LML_rbf = np.zeros((n0, n0))
# LML_white = np.zeros((n0, n0))
# LML_exp_sine = np.zeros((n0, n0))

# for i in range(n0):
#     for j in range(n0):
#         # Current hyperparameters of the model
#         current_theta = gpr_model.kernel_.theta
        
#         # For RBF kernel
#         theta_rbf = np.log([Theta0[i, j]])
#         complete_theta_rbf = np.concatenate([current_theta[1:], theta_rbf])
#         LML_rbf[i, j] = gpr_model.log_marginal_likelihood(theta=complete_theta_rbf, eval_gradient=True)[]
        
#         # For WhiteKernel
#         theta_white = np.log([Theta1[i, j]])
#         complete_theta_white = np.concatenate([np.array([current_theta[0]]), theta_white, current_theta[2:3]])
#         LML_white[i, j] = gpr_model.log_marginal_likelihood(theta=complete_theta_white, eval_gradient=True)[1]
        
#         # For ExpSineSquared kernel
#         theta_exp_sine = np.log([Theta2[i, j], Theta3[i, j]])
#         complete_theta_exp_sine = np.concatenate([current_theta[:2], theta_exp_sine])
#         LML_exp_sine[i, j] = gpr_model.log_marginal_likelihood(theta=complete_theta_exp_sine, eval_gradient=True)[1]

# # Visualization using Plotly
# fig = go.Figure()

# # LML heatmap for RBF kernel
# fig.add_trace(go.Contour(z=LML_rbf, x=theta0, y=theta1, colorscale='Viridis', name='RBF'))

# # LML heatmap for WhiteKernel
# fig.add_trace(go.Contour(z=LML_white, x=theta0, y=theta1, colorscale='Viridis', name='WhiteKernel'))

# # LML heatmap for ExpSineSquared kernel
# fig.add_trace(go.Contour(z=LML_exp_sine, x=theta2, y=theta3, colorscale='Viridis', name='ExpSineSquared'))

# fig.update_layout(title='Log Marginal Likelihood Heatmaps', xaxis_title='Length Scale / Noise Level', yaxis_title='Length Scale / Periodicity')
# fig.show()


<h1> Exp 3: clipping the gaps

In [34]:
import pandas as pd
import plotly.graph_objects as go
from statsmodels.tsa.stattools import adfuller

# Assuming data_df is your DataFrame and 'centered_car_count' is the column you're analyzing
series = data_df['centered_car_count']

# 1. Visualize the time series
fig = go.Figure()
fig.add_trace(go.Scatter(x=series.index, y=series, mode='lines', name='Original Series'))
fig.update_layout(title='Time Series', xaxis_title='Date', yaxis_title='Value')
fig.show()

# 2. Perform the ADF test
result = adfuller(series)
print('ADF Statistic:', result[0])
print('p-value:', result[1])
print('Critical Values:', result[4])

# A rule of thumb to interpret the p-value:
if result[1] <= 0.05:
    print("The series is stationary.")
else:
    print("The series is not stationary.")

# 3. Visualize the rolling mean and standard deviation
rolling_mean = series.rolling(window=12).mean()
rolling_std = series.rolling(window=12).std()

fig = go.Figure()
fig.add_trace(go.Scatter(x=series.index, y=series, mode='lines', name='Original Series'))
fig.add_trace(go.Scatter(x=rolling_mean.index, y=rolling_mean, mode='lines', name='Rolling Mean'))
fig.add_trace(go.Scatter(x=rolling_std.index, y=rolling_std, mode='lines', name='Rolling Std Dev'))
fig.update_layout(title='Rolling Mean & Standard Deviation', xaxis_title='Date', yaxis_title='Value')
fig.show()


ADF Statistic: -4.977929188012697
p-value: 2.45369692357087e-05
Critical Values: {'1%': -3.4371587399783072, '5%': -2.8645459603872903, '10%': -2.568370536787406}
The series is stationary.


<h1> Exp 4: hour_of_day feature

In [35]:
# Partial normalisation here 
data_df = data_df.sort_index()  # Ensure the data is sorted by timestamp

# feature to shift the mean on y axis to 0, normalization 
data_df['centered_car_count'] = data_df['car_count'] - data_df['car_count'].mean() 
data_length = len(data_df)

In [36]:
data_df.info()

<class 'pandas.core.frame.DataFrame'>
DatetimeIndex: 968 entries, 2023-06-06 20:36:00 to 2023-08-14 13:26:00
Data columns (total 14 columns):
 #   Column              Non-Null Count  Dtype  
---  ------              --------------  -----  
 0   car_count           968 non-null    int64  
 1   num_timestamp       968 non-null    int64  
 2   month_no            968 non-null    int32  
 3   month_name          968 non-null    object 
 4   day                 968 non-null    int32  
 5   day_of_week         968 non-null    int32  
 6   day_of_week_name    968 non-null    object 
 7   is_weekend          968 non-null    int64  
 8   hour_of_day         968 non-null    int32  
 9   minutes             968 non-null    int32  
 10  min_of_day          968 non-null    int32  
 11  week_no             968 non-null    int32  
 12  combined            968 non-null    object 
 13  centered_car_count  968 non-null    float64
dtypes: float64(1), int32(7), int64(3), object(3)
memory usage: 87.0+ KB


In [37]:
data_df

car_count  num_timestamp  month_no month_name  day  \
timestamp_true                                                            
2023-06-06 20:36:00          5       28101396         6       June    6   
2023-06-06 21:06:00          9       28101426         6       June    6   
2023-06-06 21:37:00          4       28101457         6       June    6   
2023-06-06 22:07:00          7       28101487         6       June    6   
2023-06-06 22:37:00          6       28101517         6       June    6   
...                        ...            ...       ...        ...  ...   
2023-08-14 11:26:00          2       28200206         8     August   14   
2023-08-14 11:56:00          2       28200236         8     August   14   
2023-08-14 12:26:00          2       28200266         8     August   14   
2023-08-14 12:56:00          3       28200296         8     August   14   
2023-08-14 13:26:00          2       28200326         8     August   14   

                     day_of_week day_of_week_name  is_weekend  hour_of_day  \
timestamp_true                                                               
2023-06-06 20:36:00            1          Tuesday           0           20   
2023-06-06 21:06:00            1          Tuesday           0           21   
2023-06-06 21:37:00            1          Tuesday           0           21   
2023-06-06 22:07:00            1          Tuesday           0           22   
2023-06-06 22:37:00            1          Tuesday           0           22   
...                          ...              ...         ...          ...   
2023-08-14 11:26:00            0           Monday           0           11   
2023-08-14 11:56:00            0           Monday           0           11   
2023-08-14 12:26:00            0           Monday           0           12   
2023-08-14 12:56:00            0           Monday           0           12   
2023-08-14 13:26:00            0           Monday           0           13   

                     minutes  min_of_day  week_no  combined  \
timestamp_true                                                
2023-06-06 20:36:00       36        1236        1  06062036   
2023-06-06 21:06:00        6        1266        1  06062106   
2023-06-06 21:37:00       37        1297        1  06062137   
2023-06-06 22:07:00        7        1327        1  06062207   
2023-06-06 22:37:00       37        1357        1  06062237   
...                      ...         ...      ...       ...   
2023-08-14 11:26:00       26         686        0  08141126   
2023-08-14 11:56:00       56         716        0  08141156   
2023-08-14 12:26:00       26         746        0  08141226   
2023-08-14 12:56:00       56         776        0  08141256   
2023-08-14 13:26:00       26         806        0  08141326   

                     centered_car_count  
timestamp_true                           
2023-06-06 20:36:00           -8.046488  
2023-06-06 21:06:00           -4.046488  
2023-06-06 21:37:00           -9.046488  
2023-06-06 22:07:00           -6.046488  
2023-06-06 22:37:00           -7.046488  
...                                 ...  
2023-08-14 11:26:00          -11.046488  
2023-08-14 11:56:00          -11.046488  
2023-08-14 12:26:00          -11.046488  
2023-08-14 12:56:00          -10.046488  
2023-08-14 13:26:00          -11.046488  

[968 rows x 14 columns]

In [38]:
fig = go.Figure()

fig.add_trace(go.Scatter(x= data_df['num_timestamp'], y= data_df['car_count'], name= "orignial"))
fig.add_trace(go.Scatter(x= data_df['num_timestamp'], y= data_df['centered_car_count'], name= "Centered"))

fig.update_layout(title_text= "Centering counts", xaxis_title= "time", yaxis_title= "Counts", showlegend= True)

fig.show()

In [39]:
data_df_trunc = data_df[['car_count', 'month_no', 'day', 'day_of_week', 'hour_of_day', 'min_of_day', 'centered_car_count','combined']]

In [40]:
 
day_mean_df = data_df_trunc.groupby('hour_of_day').mean().reset_index()
day_med_df = data_df_trunc.groupby('hour_of_day').median().reset_index()

In [41]:
day_mean_df

hour_of_day  car_count  month_no        day  day_of_week   min_of_day  \
0             0   5.921053  6.894737  12.157895     3.131579    29.736842   
1             1   5.875000  7.000000  11.875000     3.425000    87.950000   
2             2   5.404762  6.952381  12.166667     3.047619   149.047619   
3             3   7.263158  7.000000  11.552632     3.342105   207.921053   
4             4  10.277778  7.000000  11.194444     3.250000   268.222222   
5             5  11.432432  6.972973  11.432432     3.189189   328.864865   
6             6  11.324324  6.972973  11.405405     3.351351   389.486486   
7             7  10.368421  6.947368  11.947368     3.236842   449.973684   
8             8  13.540541  6.972973  11.405405     3.351351   509.648649   
9             9  16.756098  6.878049  12.121951     3.000000   568.853659   
10           10  17.500000  6.947368  11.815789     3.105263   628.315789   
11           11  19.372093  6.837209  13.162791     2.930233   689.883721   
12           12  16.315789  6.947368  11.131579     3.342105   751.052632   
13           13  19.380952  6.904762  11.309524     3.071429   809.095238   
14           14  19.204082  6.816327  12.306122     2.918367   871.122449   
15           15  19.395349  6.930233  11.395349     3.023256   931.372093   
16           16  17.590909  6.863636  11.545455     2.977273   990.545455   
17           17  18.146341  6.878049  11.658537     2.878049  1049.756098   
18           18  16.100000  6.900000  11.400000     2.875000  1108.350000   
19           19  14.225000  6.900000  11.700000     3.000000  1167.775000   
20           20  11.500000  6.818182  11.886364     2.886364  1227.227273   
21           21   9.512195  6.878049  10.243902     3.000000  1288.097561   
22           22   7.604651  6.837209  10.883721     3.093023  1348.674419   
23           23   5.552632  6.947368  10.710526     2.921053  1408.368421   

    centered_car_count                                           combined  
0            -7.125435  1597370542289573826333388940671159368705584817...  
1            -7.171488                                                inf  
2            -7.641726                                                inf  
3            -5.783330  1597450015974579082089030347760218723608493277...  
4            -2.768710  1686225016862336502354225514249428607792323499...  
5            -1.614055  1640678665055516321135309866369576322998904625...  
6            -1.722163  1640705692082816196378626994764855320028536974...  
7            -2.678067  1597555805449321079808740220113152149957530487...  
8             0.494053  1640760286677954343194219084947811732301452175...  
9             3.709610                                                inf  
10            4.453512  1597635279134326335564381627202211504860438946...  
11            6.325605                                                inf  
12            3.269302  1597688173871697453385589241601323241879957403...  
13            6.334465                                                inf  
14            6.157594                                                inf  
15            6.348861                                                inf  
16            4.544421                                                inf  
17            5.099854                                                inf  
18            3.053512                                                inf  
19            1.178512                                                inf  
20           -1.546488                                                inf  
21           -3.534292                                                inf  
22           -5.441836                                                inf  
23           -7.493856  1595343963321942302752939302575691319426415993...

In [42]:
day_med_df

hour_of_day  car_count  month_no   day  day_of_week  min_of_day  \
0             0        6.0       6.0  10.5          3.0        34.0   
1             1        5.5       7.0  10.5          3.0        87.0   
2             2        4.0       6.0  11.0          3.0       152.0   
3             3        6.0       7.0  10.0          3.0       207.0   
4             4        8.0       7.0  10.0          3.0       269.5   
5             5       12.0       6.0  10.0          3.0       330.0   
6             6       12.0       6.0  10.0          3.0       386.0   
7             7        8.0       6.0  10.0          3.0       452.0   
8             8       15.0       6.0  10.0          3.0       508.0   
9             9       19.0       6.0  11.0          3.0       565.0   
10           10       20.5       6.0  10.0          3.0       625.0   
11           11       24.0       6.0  11.0          3.0       692.0   
12           12       18.0       6.0  10.0          3.0       751.0   
13           13       24.5       6.0  10.0          3.0       806.5   
14           14       24.0       6.0  10.0          3.0       871.0   
15           15       22.0       6.0  10.0          3.0       931.0   
16           16       20.5       6.0  10.0          3.0       990.0   
17           17       21.0       6.0  10.0          3.0      1051.0   
18           18       16.5       6.0  10.0          3.0      1110.5   
19           19       11.5       6.0  10.0          3.0      1169.5   
20           20        8.5       6.0  10.0          3.0      1227.5   
21           21        9.0       6.0   9.0          3.0      1292.0   
22           22        8.0       6.0   9.0          3.0      1352.0   
23           23        5.0       6.0   9.0          3.0      1410.5   

    centered_car_count   combined  
0            -7.046488  6260033.5  
1            -7.546488  7145126.0  
2            -9.046488  6260240.5  
3            -7.046488  7145329.5  
4            -5.046488  7145428.0  
5            -1.046488  6260557.0  
6            -1.046488  6260656.0  
7            -5.046488  6260749.5  
8             1.953512  6260817.0  
9             5.953512  6200951.0  
10            7.453512  6261020.5  
11           10.953512  6261112.0  
12            4.953512  6256218.5  
13           11.453512  6261314.0  
14           10.953512  6251410.0  
15            8.953512  6261535.0  
16            7.453512  6246654.0  
17            7.953512  6241754.0  
18            3.453512  6251845.5  
19           -1.546488  6256925.0  
20           -4.546488  6242021.5  
21           -4.046488  6242128.0  
22           -5.046488  6242238.0  
23           -8.046488  6252325.0

In [43]:

# Create a new figure
fig = go.Figure()

# Add a trace for day_mean_df's car_count
fig.add_trace(go.Scatter(x=day_mean_df['hour_of_day'], 
                         y=day_mean_df['car_count'], 
                         mode='markers', 
                         name='Mean Car Count'))

# Add a trace for day_mean_df's centered_car_count
fig.add_trace(go.Scatter(x=day_mean_df['hour_of_day'], 
                         y=day_mean_df['centered_car_count'], 
                         mode='markers', 
                         name='Mean Centered Car Count'))

# Add a trace for day_med_df's car_count
fig.add_trace(go.Scatter(x=day_med_df['hour_of_day'], 
                         y=day_med_df['car_count'], 
                         mode='markers', 
                         name='Median Car Count'))

# Add a trace for day_med_df's centered_car_count
fig.add_trace(go.Scatter(x=day_med_df['hour_of_day'], 
                         y=day_med_df['centered_car_count'], 
                         mode='markers', 
                         name='Median Centered Car Count'))

# Update layout for better visualization
fig.update_layout(title='Comparison of Mean and Median Aggregations',
                  xaxis_title='Hour of Day',
                  yaxis_title='Count',
                  legend_title='Aggregations')

fig.show()


In [44]:
# Setting the split ratios
train_ratio = 0.6
valid_ratio = 0.2
# test_ratio is implicitly set as 0.2 (remaining portion)

def split_data(df, features, target):
    train_idx = int(train_ratio * len(df))
    valid_idx = train_idx + int(valid_ratio * len(df))
    
    # Splitting data into train, valid, and test
    train = df.iloc[:train_idx]
    valid = df.iloc[train_idx:valid_idx]
    test = df.iloc[valid_idx:]
    
    # Splitting features (X) and ensuring they're reshaped
    X_train = train[features].values.reshape(-1, 1)
    X_valid = valid[features].values.reshape(-1, 1)
    X_test = test[features].values.reshape(-1, 1)
    
    # Splitting target (y)
    y_train = train[target]
    y_valid = valid[target]
    y_test = test[target]
    
    return X_train, y_train, X_valid, y_valid, X_test, y_test





In [45]:
from statsmodels.tsa.stattools import adfuller
def ad_fuller_test(series):
    res = adfuller(series)
    print('ADF Statistic:', res[0])
    print('p-value:', res[1])
    print('Critical Values:', res[4])

    # A rule of thumb to interpret the p-value:
    if res[1] <= 0.05:
        print("The series is stationary.")
    else:
        print("The series is not stationary.")
   
    



In [46]:
ad_fuller_test(day_mean_df['centered_car_count'])
ad_fuller_test(day_med_df['centered_car_count'])

ADF Statistic: -1.8307958779034694
p-value: 0.36528309622415844
Critical Values: {'1%': -4.01203360058309, '5%': -3.1041838775510207, '10%': -2.6909873469387753}
The series is not stationary.
ADF Statistic: -2.5923336280910845
p-value: 0.09459212537091738
Critical Values: {'1%': -4.01203360058309, '5%': -3.1041838775510207, '10%': -2.6909873469387753}
The series is not stationary.


In [47]:
X_mean=  day_mean_df['hour_of_day'].values.reshape(-1,1)
y_mean = day_mean_df['centered_car_count'].values.reshape(-1,1)

In [48]:
from sklearn.gaussian_process.kernels import RBF, WhiteKernel, ExpSineSquared, ConstantKernel as C

# RBF kernel with a length scale of 1.0
k1 = 1 * RBF(length_scale=0.5, length_scale_bounds=(1e-3, 1e3))

# White kernel to account for noise
k2 = WhiteKernel(noise_level=1, noise_level_bounds=(1e-10, 1e+1))

# Periodic kernel
k3 = ExpSineSquared(length_scale=1.0,
                    length_scale_bounds=(1e-1, 50) ,
                    periodicity=1,
                    periodicity_bounds= (1e-1, 50))

# Combined kernel
kernel = k1 + k2 + k3

gpr = GaussianProcessRegressor(kernel=kernel, n_restarts_optimizer= 10)

In [49]:
plot_gpr_samples_plotly(gpr, 5, X_mean, y_mean)


gpr.fit(X_mean ,y_mean)

y_pred, y_std = gpr.predict(X_mean, return_std=True)

plot_gpr_samples_plotly(gpr, 5, X_mean,y_mean)

# Compute evaluation metrics
mae = mean_absolute_error(y_mean, y_pred)
mse = mean_squared_error(y_mean, y_pred)
rmse = np.sqrt(mse)
r2 = r2_score(y_mean, y_pred)
mape = np.mean(np.abs((y_mean - y_pred) / y_mean)) * 100

# Extract kernel parameters and other model-specific info
kernel_params = gpr.kernel_.get_params()
noise_level = kernel_params.get("k2__noise_level", None)  # Assumes WhiteKernel is named "k2"
lml = gpr.log_marginal_likelihood()

# Print the metrics and information
print(f"MAE: {mae}")
print(f"MSE: {mse}")
print(f"RMSE: {rmse}")
print(f"R-squared: {r2}")
print(f"MAPE: {mape}%")
print(f'LML: {lml}')
      
print(f"Kernel parameters after fit: \n{gpr.kernel_} \n")
print(f"noise level: {noise_level}")

print("Predicted values:", y_pred)
print("Learned kernel parameters:", kernel_params)


MAE: 0.20150356905181185
MSE: 0.07237168430529986
RMSE: 0.2690198585705149
R-squared: 0.9969784572505327
MAPE: 180.82939540481274%
LML: -47.31994372917821
Kernel parameters after fit: 
8.8**2 * RBF(length_scale=8.26) + WhiteKernel(noise_level=0.302) + ExpSineSquared(length_scale=0.18, periodicity=22) 

noise level: None
Predicted values: [-7.23362537 -7.15022759 -7.32394039 -5.67552689 -3.09202242 -1.87470219
 -1.7895644  -2.13222508  0.58932959  3.41276554  4.47738555  5.83266738
  3.98939887  6.11546538  6.25654179  6.16966171  4.78799548  4.79937794
  3.01593921  1.06737317 -1.45097209 -3.4847439  -5.32756528 -7.48828464]
Learned kernel parameters: {'k1': 8.8**2 * RBF(length_scale=8.26) + WhiteKernel(noise_level=0.302), 'k2': ExpSineSquared(length_scale=0.18, periodicity=22), 'k1__k1': 8.8**2 * RBF(length_scale=8.26), 'k1__k2': WhiteKernel(noise_level=0.302), 'k1__k1__k1': 8.8**2, 'k1__k1__k2': RBF(length_scale=8.26), 'k1__k1__k1__constant_value': 77.49203505348459, 'k1__k1__k1__con

In [50]:
X_med=  day_med_df['hour_of_day'].values.reshape(-1,1)
y_med = day_med_df['centered_car_count'].values.reshape(-1,1)

In [51]:
plot_gpr_samples_plotly(gpr, 5, X_med, y_med)


gpr.fit(X_med ,y_med)

y_pred, y_std = gpr.predict(X_med, return_std=True)

plot_gpr_samples_plotly(gpr, 5, X_med,y_med)

# Compute evaluation metrics
mae = mean_absolute_error(y_med, y_pred)
mse = mean_squared_error(y_med, y_pred)
rmse = np.sqrt(mse)
r2 = r2_score(y_med, y_pred)
mape = np.mean(np.abs((y_med - y_med) / y_med)) * 100

# Extract kernel parameters and other model-specific info
kernel_params = gpr.kernel_.get_params()
noise_level = kernel_params.get("k2__noise_level", None)  # Assumes WhiteKernel is named "k2"
lml = gpr.log_marginal_likelihood()

# Print the metrics and information
print(f"MAE: {mae}")
print(f"MSE: {mse}")
print(f"RMSE: {rmse}")
print(f"R-squared: {r2}")
print(f"MAPE: {mape}%")
print(f'LML: {lml}')
      
print(f"Kernel parameters after fit: \n{gpr.kernel_} \n")
print(f"noise level: {noise_level}")

print("Predicted values:", y_pred)
print("Learned kernel parameters:", kernel_params)


MAE: 1.1011347027961669
MSE: 2.5528121078322688
RMSE: 1.5977522047652661
R-squared: 0.9449234570661802
MAPE: 0.0%
LML: -60.622439152681935
Kernel parameters after fit: 
8.27**2 * RBF(length_scale=6.17) + WhiteKernel(noise_level=3.57) + ExpSineSquared(length_scale=1.09, periodicity=1.31) 

noise level: None
Predicted values: [-7.4557854  -6.99350869 -7.59916824 -7.5596704  -5.35959247 -2.97737236
 -2.06718872 -0.86972788  1.91885984  5.46440723  6.85546797  7.62493707
  8.92622293 11.06712723 10.58422398  8.65323016  6.71251554  6.08738149
  3.67278046 -0.05102515 -3.27847939 -4.31416699 -5.52691826 -7.80050444]
Learned kernel parameters: {'k1': 8.27**2 * RBF(length_scale=6.17) + WhiteKernel(noise_level=3.57), 'k2': ExpSineSquared(length_scale=1.09, periodicity=1.31), 'k1__k1': 8.27**2 * RBF(length_scale=6.17), 'k1__k2': WhiteKernel(noise_level=3.57), 'k1__k1__k1': 8.27**2, 'k1__k1__k2': RBF(length_scale=6.17), 'k1__k1__k1__constant_value': 68.35144678687708, 'k1__k1__k1__constant_value

In [52]:
from sklearn.gaussian_process.kernels import RationalQuadratic
from sklearn.gaussian_process.kernels import RBF, WhiteKernel, ExpSineSquared, ConstantKernel as C

rq_kernel = 1.0 * RationalQuadratic(length_scale=1, alpha=0.5, alpha_bounds=(1e-05, 1e15))
gpr = GaussianProcessRegressor(kernel=rq_kernel, random_state=0)

plot_gpr_samples_plotly(gpr, 5, X_mean, y_mean)


gpr.fit(X_mean ,y_mean)

y_pred, y_std = gpr.predict(X_mean, return_std=True)

plot_gpr_samples_plotly(gpr, 5, X_mean,y_mean)

# Compute evaluation metrics
mae = mean_absolute_error(y_mean, y_pred)
mse = mean_squared_error(y_mean, y_pred)
rmse = np.sqrt(mse)
r2 = r2_score(y_mean, y_pred)
mape = np.mean(np.abs((y_mean - y_pred) / y_mean)) * 100

# Extract kernel parameters and other model-specific info
kernel_params = gpr.kernel_.get_params()
noise_level = kernel_params.get("k2__noise_level", None)  # Assumes WhiteKernel is named "k2"
lml = gpr.log_marginal_likelihood()

# Print the metrics and information
print(f"MAE: {mae}")
print(f"MSE: {mse}")
print(f"RMSE: {rmse}")
print(f"R-squared: {r2}")
print(f"MAPE: {mape}%")
print(f'LML: {lml}')
      
print(f"Kernel parameters after fit: \n{gpr.kernel_} \n")
print(f"noise level: {noise_level}")

print("Predicted values:", y_pred)
print("Learned kernel parameters:", kernel_params)



/home/sf_afn/usr_sa/anaconda3/envs/prkng_v2_env/lib/python3.11/site-packages/sklearn/gaussian_process/kernels.py:419: ConvergenceWarning:

The optimal value found for dimension 0 of parameter k2__length_scale is close to the specified lower bound 1e-05. Decreasing the bound and calling fit again may find a better value.



MAE: 1.833413051007445e-11
MSE: 4.1711122002536525e-22
RMSE: 2.0423300909142118e-11
R-squared: 1.0
MAPE: 182.07687776461938%
LML: -72.17806558086079
Kernel parameters after fit: 
4.9**2 * RationalQuadratic(alpha=1.24e+06, length_scale=1e-05) 

noise level: None
Predicted values: [-7.12543497 -7.1714876  -7.6417257  -5.78332971 -2.76870983 -1.61405517
 -1.72216328 -2.67806655  0.49405294  3.70960996  4.4535124   6.32560542
  3.26930187  6.33446478  6.15759403  6.34886123  4.54442149  5.09985386
  3.0535124   1.1785124  -1.5464876  -3.53429248 -5.44183644 -7.49385602]
Learned kernel parameters: {'k1': 4.9**2, 'k2': RationalQuadratic(alpha=1.24e+06, length_scale=1e-05), 'k1__constant_value': 23.973803854651845, 'k1__constant_value_bounds': (1e-05, 100000.0), 'k2__length_scale': 9.999999999999997e-06, 'k2__alpha': 1239155.6326074358, 'k2__length_scale_bounds': (1e-05, 100000.0), 'k2__alpha_bounds': (1e-05, 1000000000000000.0)}


In [53]:
length_scale=1.0
length_scale_bounds=(1e-05, 1e15)
kernel = 1.0 * RBF(
        length_scale=length_scale, length_scale_bounds=length_scale_bounds
    )
gpr = GaussianProcessRegressor(kernel=kernel, random_state=0)